In [1]:
import pandas as pd
import joblib
import RIfunctions as ri

from pgmpy.estimators import ExhaustiveSearch, BicScore, BayesianEstimator
from pgmpy.models import BayesianNetwork

In [2]:
# from itertools import combinations

# import networkx as nx
# from sklearn.metrics import f1_score


# from pgmpy.utils import get_example_model
# from pgmpy.sampling import BayesianModelSampling

**Reference**

- https://towardsdatascience.com/bbn-bayesian-belief-networks-how-to-build-them-effectively-in-python-6b7f93435bba

In [3]:
# Read in the weather data csv
df = pd.read_csv('input_file_2.csv', sep = ',', index_col=0)

# Filter for instances that were before 2016 as we know the accepted loans default status
# and should only infer those rejected applications for the same period
df['issue_d'] = pd.to_datetime(df['issue_d'])
df = df.loc[df['issue_d'] < '2016-1-1']
df = df[['loan_amnt', 'emp_length', 'dti','purpose','charged_off']]
# May need to drop instances with 'educational' purpose value
emp_length_mean = df['emp_length'].mean()
df['emp_length'].fillna(emp_length_mean, inplace = True)

# Create bands for variables that we want to use in the model
# May need to tune the the number of intervals

df['emp_length_cat'], emp_bins = pd.qcut(df['emp_length'], q=3, retbins=True)
df['dti_cat'], dti_bins = pd.qcut(df['dti'], q=4, retbins=True)
df['loan_amnt_cat'], loan_bins = pd.qcut(df['loan_amnt'], q=4, retbins=True)

df['emp_length_cat'] = df['emp_length_cat'].astype(str)
df['dti_cat'] = df['dti_cat'].astype(str)
df['loan_amnt_cat'] = df['loan_amnt_cat'].astype(str)

emp_length_cat_lb = str(emp_bins[-1])
dti_cat_lb = str(dti_bins[-1])
loan_amnt_cat_lb = str(loan_bins[-1])

emp_length_open_cat = str(emp_bins[-2]) + " <"
dti_open_cat = str(dti_bins[-2]) + " <"
loan_amnt_open_cat = str(loan_bins[-2]) + " <"

df.loc[df["emp_length_cat"].str.contains(emp_length_cat_lb), "emp_length_cat"] = emp_length_open_cat
df.loc[df["dti_cat"].str.contains(dti_cat_lb), "dti_cat"] = dti_open_cat
df.loc[df["loan_amnt_cat"].str.contains(loan_amnt_cat_lb), "loan_amnt_cat"] = loan_amnt_open_cat

data = df.drop(['loan_amnt', 'emp_length', 'dti'], axis=1)

In [29]:
print(loan_amnt_open_cat)

20000.0 <


In [4]:
rejects = pd.read_csv('input_file_1.csv', sep = ',', index_col=0)
rejects['issue_d'] = pd.to_datetime(rejects['issue_d'])
rejects = rejects.loc[rejects['issue_d'] < '2016-1-1']
rejects = rejects.loc[rejects["rejected"] == 1]
rejects = ri.purposeCleaning(rejects)
rejects['emp_length'].fillna(emp_length_mean, inplace = True)
rejects = rejects.drop(rejects[rejects['purpose'] == 'Business'].index)
rejects.drop(['rejected', 'issue_d'], axis=1, inplace=True)

# Need to bin the reject continous variables
rejects['emp_length_cat'] = pd.cut(rejects["emp_length"], bins=emp_bins, include_lowest=True).astype(str)
rejects['dti_cat'] = pd.cut(rejects["dti"], bins=dti_bins, include_lowest=True).astype(str)
rejects['loan_amnt_cat'] = pd.cut(rejects["loan_amnt"], bins=loan_bins, include_lowest=True).astype(str)

rejects['dti_cat'].fillna(dti_open_cat, inplace = True)
rejects['loan_amnt_cat'].fillna(loan_amnt_open_cat, inplace = True)

rejects.loc[rejects["emp_length_cat"].str.contains(emp_length_cat_lb), "emp_length_cat"] = emp_length_open_cat
rejects.loc[rejects["dti_cat"].str.contains(dti_cat_lb), "dti_cat"] = dti_open_cat
rejects.loc[rejects["loan_amnt_cat"].str.contains(loan_amnt_cat_lb), "loan_amnt_cat"] = loan_amnt_open_cat

rejects = rejects.drop(['loan_amnt', 'emp_length', 'dti'], axis=1)

C:\Users\joshy\AppData\Roaming\Python\Python38\site-packages\numpy\lib\arraysetops.py:580: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  mask |= (ar1 == a)


In [5]:
print(rejects.columns)
print(list(set(rejects['purpose']) - set(df['purpose'])))
print(list(set(df['purpose']) - set(rejects['purpose'])))

Index(['purpose', 'emp_length_cat', 'dti_cat', 'loan_amnt_cat'], dtype='object')
[]
['educational', 'renewable_energy']


In [6]:
# # Create nodes by manually typing in probabilities
# emp_length = BbnNode(Variable(0, 'emp_length', ['<=60', '>60']), [0.30658, 0.69342])
# dti = BbnNode(Variable(1, 'dti', ['<=60', '>60']), [0.92827, 0.07173, 
#                                                       0.55760, 0.44240])
# loan_amnt = BbnNode(Variable(2, 'loan_amnt', ['<=40', '40-50', '>50']), [0.58660, 0.24040, 0.17300])
# purpose = BbnNode(Variable(3, 'purpose', ['<=40', '40-50', '>50']), [0.58660, 0.24040, 0.17300])
# GB = BbnNode(Variable(4, 'GB', ['No', 'Yes']), [0.92314, 0.07686, 
#                                                 0.89072, 0.10928, 
#                                                 0.76008, 0.23992, 
#                                                 0.64250, 0.35750, 
#                                                 0.49168, 0.50832, 
#                                                 0.32182, 0.67818])

In [7]:
# g=nx.DiGraph()
# g.add_edges_from(df[['loan_amnt_cat', 'emp_length_cat']].to_records(index=False))

In [8]:
# from networkx.algorithms.traversal.depth_first_search import dfs_tree

# x = dfs_tree(g,1)
# x.edges()

In [9]:
# def get_descendants(parent):
#     descendants = list(dfs_tree(g, parent).edges())
#     return [x[1] for x in descendants]

    
# df["descendants"] = df["parent"].apply(get_descendants)

In [10]:
# # This function helps to calculate probability distribution, which goes into BBN (note, can handle up to 2 parents)
# def probs(data, child, parent1=None, parent2=None):
#     if parent1==None:
#         # Calculate probabilities
#         prob=pd.crosstab(data[child], 'Empty', margins=False, normalize='columns').sort_index().to_numpy().reshape(-1).tolist()
#     elif parent1!=None:
#             # Check if child node has 1 parent or 2 parents
#             if parent2==None:
#                 # Caclucate probabilities
#                 prob=pd.crosstab(data[parent1],data[child], margins=False, normalize='index').sort_index().to_numpy().reshape(-1).tolist()
#             else:    
#                 # Caclucate probabilities
#                 prob=pd.crosstab([data[parent1],data[parent2]],data[child], margins=False, normalize='index').sort_index().to_numpy().reshape(-1).tolist()
#     else: print("Error in Probability Frequency Calculations")
#     return prob  

In [11]:
# Network structure optimisation

scoring_method = BicScore(data=df)
# est = HillClimbSearch(data=df)
est = ExhaustiveSearch(data=data, scoring_method=scoring_method)
estimated_model = est.estimate()

print(estimated_model.edges())

print("\nAll DAGs by score:")
for score, dag in reversed(est.all_scores()):
    print(score, dag.edges())

[('dti_cat', 'charged_off'), ('emp_length_cat', 'charged_off'), ('emp_length_cat', 'loan_amnt_cat'), ('loan_amnt_cat', 'charged_off'), ('loan_amnt_cat', 'dti_cat'), ('purpose', 'dti_cat'), ('purpose', 'emp_length_cat'), ('purpose', 'loan_amnt_cat')]

All DAGs by score:
-3630116.357186811 [('emp_length_cat', 'loan_amnt_cat'), ('emp_length_cat', 'charged_off'), ('loan_amnt_cat', 'charged_off'), ('loan_amnt_cat', 'dti_cat'), ('dti_cat', 'charged_off'), ('purpose', 'dti_cat'), ('purpose', 'emp_length_cat'), ('purpose', 'loan_amnt_cat')]
-3630116.3571868115 [('dti_cat', 'charged_off'), ('emp_length_cat', 'charged_off'), ('loan_amnt_cat', 'charged_off'), ('loan_amnt_cat', 'dti_cat'), ('loan_amnt_cat', 'emp_length_cat'), ('purpose', 'dti_cat'), ('purpose', 'emp_length_cat'), ('purpose', 'loan_amnt_cat')]
-3630116.3571868115 [('loan_amnt_cat', 'purpose'), ('loan_amnt_cat', 'charged_off'), ('loan_amnt_cat', 'dti_cat'), ('loan_amnt_cat', 'emp_length_cat'), ('purpose', 'dti_cat'), ('purpose', 'em

In [12]:
model = BayesianNetwork(estimated_model)
model.fit(data, estimator=BayesianEstimator, prior_type="BDeu") # Bayesian Dirichlet equivalent uniform prior
for cpd in model.get_cpds():
    print(cpd)


+----------------+-----+------------------------+
| dti_cat        | ... | dti_cat(23.37 <)       |
+----------------+-----+------------------------+
| emp_length_cat | ... | emp_length_cat(9.0 <)  |
+----------------+-----+------------------------+
| loan_amnt_cat  | ... | loan_amnt_cat(35000.0) |
+----------------+-----+------------------------+
| charged_off(0) | ... | 0.6968612434116267     |
+----------------+-----+------------------------+
| charged_off(1) | ... | 0.30313875658837325    |
+----------------+-----+------------------------+
+--------------------------+-----+------------------------+
| loan_amnt_cat            | ... | loan_amnt_cat(35000.0) |
+--------------------------+-----+------------------------+
| purpose                  | ... | purpose(wedding)       |
+--------------------------+-----+------------------------+
| dti_cat((-0.001, 11.57]) | ... | 0.4082004435526455     |
+--------------------------+-----+------------------------+
| dti_cat((11.57, 17.22])  | .

In [13]:
# Saving the model

joblib.dump(model, "./BN model.joblib")

['./BN model.joblib']

In [28]:
y_prob = model.predict_probability(rejects)

100%|██████████| 654/654 [00:06<00:00, 94.52it/s] 
